In [63]:
#import everything upwards from home dir
from __future__ import absolute_import
from googleapiclient.discovery import build
from googleapiclient import http
from oauth2client.service_account import ServiceAccountCredentials
from configparser import ConfigParser
import psycopg2
import argparse
import sys
import google.ads.google_ads.client
import pandas as pd
import re
import numpy as np
import time
import datetime
from xlrd import XLRDError

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', None)

def google_analytics(df_conf_req, view_id, key_file_location, scopes):
    
    
    # Initializes an Analytics Reporting API V4 service object.
    try:
        credentials = ServiceAccountCredentials.from_json_keyfile_name(
                key_file_location, scopes)
    except(NameError, IOError, FileNotFoundError) as error:
        print('Could not read configuration file(s)')
        print(error)
        sys.exit(1)   

    # Build the service object.
    analytics = build('analyticsreporting', 'v4', credentials=credentials)
    
    # define empty pandas dataframe
    df_response = pd.DataFrame()
    
    # create lists for metrics and dimensions
    dim_lst = []
    met_lst = []
    start_date = df_conf_req.iat[0,2]
    end_date = df_conf_req.iat[1,2]
    for index, req in df_conf_req.iterrows():
        if not 'nan' in str(req['dimensions']):
            dim_lst.append(dict({'name':req['dimensions']}))
        if not 'nan' in str(req['metrics']):
            met_lst.append(dict({'expression':req['metrics']}))  
    
    dim_met_lst = dim_lst +  met_lst
    
    met_batches = list()
    
    # split metric list into batches, since a single API call can have a max of 10 metrics
    i = 0
    while True:
        met_batch = list()
        stop = 0
        for index, met in enumerate(met_lst):
            if len(met_batch) < 10 and i < len(met_lst):
                res = met_batch.append(met_lst[i])
                i=i+1
        if len(met_batch) != 0:
            met_batches.append(met_batch)
        if i == len(met_lst):
            x = True
            break 

    # create empty dataframe for response segment
    
    print('Calling Google Analytics API...')
    
    try:
        # iterate over metric batches
        for index, batch in enumerate(met_batches):
            
            # define request body
            body={
            'reportRequests': [
            {
                'viewId': view_id,
                'dateRanges': [{'startDate': start_date, 'endDate': end_date}],
                'metrics': batch,
                'dimensions': dim_lst,

                'pageSize': 10000,
                'includeEmptyRows': True

            }]
            }    
            # make the call to Google Analytics API
            response = analytics.reports().batchGet(body=body).execute()
            
            df_res_part = pd.DataFrame()
            
            # deconstruct JSON response
            for report in response.get('reports', []):
                columnHeader = report.get('columnHeader', {})
                dimensionHeaders = columnHeader.get('dimensions', [])
                metricHeaders = columnHeader.get('metricHeader', {}).get('metricHeaderEntries', [])

                # iterate over rows
                for data_row in report.get('data', {}).get('rows', []):
                    dimensions = data_row.get('dimensions', [])
                    dateRangeValues = data_row.get('metrics', [])
                    var_dict = {}

                    #iterate over dimensions
                    for header, dimension in zip(dimensionHeaders, dimensions):
                        if header not in df_res_part:
                            df_res_part[header] = pd.Series()
                            df_res_part.astype({header: 'object'}).dtypes
                        var_dict.update({header : str(dimension)})

                    # iterate over metrics
                    for i, values in enumerate(dateRangeValues):
                        for metricHeader, value in zip(metricHeaders, values.get('values')):
                            if metricHeader.get('name') not in df_res_part.columns:
                                df_res_part[metricHeader.get('name')] = pd.Series()
                            var_dict.update({metricHeader.get('name') : value})
                    df_res_part = df_res_part.append(var_dict, ignore_index=True)
        
            # if iteration is first and main dataframe is empty assign current response segment
            if df_response.empty:
                df_response = df_res_part
            # else do a left join and combine the two
            else:
                df_response = pd.merge(df_response, df_res_part,  how='inner', on=['ga:campaign', 'ga:adcontent', 'ga:channelGrouping', 'ga:keyword', 'ga:date', 'ga:sourceMedium'])
            row_count_part = len(df_res_part.index)
            row_count_full = len(df_response.index)
            print('Batch ' + str(index + 1))
            print(str(row_count_full) + ' row(s) received')

    except(http.HttpError) as error:
        print('API error')
        print(error)  
        sys.exit(1)
            
    return df_response, dim_met_lst

def db_config(filename='database.ini', section='postgresql'):
    # create a parser
    parser = ConfigParser()
    # read config file
    parser.read(filename)
 
    # get section, default to postgresql
    db = {}
    if parser.has_section(section):
        params = parser.items(section)
        for param in params:
            db[param[0]] = param[1]
    else:
        raise Exception('Section {0} not found in the {1} file'.format(section, filename))
    return db

def postgre_write(df_response, dim_lst, view_id):
    #Connect to the PostgreSQL database server
    conn = None
    # read connection parameters
    params = db_config()
    
    # connect to the PostgreSQL server
    print('Connecting to the PostgreSQL database...')
    conn = psycopg2.connect(**params)
 
    try:
        # create a cursor
        cur = conn.cursor()

        # execute db write statements
        # *tread lightly* cur.execute("DROP TABLE google_analytics_temp;")
        cur.execute("CREATE TABLE IF NOT EXISTS google_analytics_temp("
                       "creation_ts TIMESTAMP , "
                       "last_updated_ts TIMESTAMP, "
                       "ga_viewID bigint, "
                       "ga_sourceMedium VARCHAR(200), "
                       "ga_date DATE, "
                       "ga_campaign VARCHAR(150), "
                       "ga_adcontent VARCHAR(150), "
                       "ga_channelGrouping VARCHAR(150), "
                       "ga_keyword VARCHAR(150), "
                       "CONSTRAINT table_analytics_pk PRIMARY KEY (ga_viewID, ga_sourceMedium, ga_date, ga_campaign, ga_adcontent, ga_channelGrouping, ga_keyword));")
        conn.commit()    
        row_count = 0
        print('Working...')
        # iterate over rows in response
        for i, row in df_response.iterrows():
            row_count = i
            creation_ts = datetime.datetime.now()
            last_updated_ts = datetime.datetime.now()
            
            ins_query_dim ='ga_viewID, creation_ts, last_updated_ts, '
            ins_query_val = f"{view_id}, '{creation_ts}', '{last_updated_ts}', "
            upd_query = f"last_updated_ts = '{last_updated_ts}', "
            col_dtype = ''
            
            # iterate over parameters in every row
            for idx, dim in enumerate(list(row.index)):
                db_dim = dim
                val = str(row[dim])
                
                # replace DB illegal char with info string
                uns_char_lst = ["'", ":"]
                for char in uns_char_lst:
                    if char in str(row[dim]):
                        val = val.replace(char, "_uns_char_fnd_ascii_dec_expr_" + str(ord(char)))
                    if char in db_dim:
                        db_dim = db_dim.replace(char, '_')
                # conditionals for variable type assignment
                if str(row[dim]) != 'nan':
                    if str(db_dim) == 'ga_sessions':
                        col_dtype = 'bigint'
                        cur.execute(f"ALTER TABLE google_analytics_temp "
                                    f"ADD COLUMN IF NOT EXISTS {db_dim} {col_dtype};")
                        ins_query_dim = ins_query_dim + db_dim + ','
                        ins_query_val = ins_query_val + " '" + val + "',"
                        upd_query = upd_query + db_dim + ' = ' + val + ', '
                        
                    elif 'goal' in str(db_dim) or 'transaction' in str(db_dim):
                        col_dtype = 'real'
                        cur.execute(f"ALTER TABLE google_analytics_temp "
                                    f"ADD COLUMN IF NOT EXISTS {db_dim} {col_dtype};")
                        ins_query_dim = ins_query_dim + db_dim + ','
                        ins_query_val = ins_query_val + " '" + val + "',"
                        upd_query = upd_query + db_dim + ' = ' + val + ', '
                    else:
                        col_dtype = 'varchar (150)'
                        cur.execute(f"ALTER TABLE google_analytics_temp "
                                    f"ADD COLUMN IF NOT EXISTS {db_dim} {col_dtype};")
                        ins_query_dim = ins_query_dim + db_dim + ','
                        ins_query_val = ins_query_val + " '" + val + "',"
            ins_query_dim = ins_query_dim[:-1]
            ins_query_val = ins_query_val[:-1]
            upd_query = upd_query[:-2]

            # insert into db or if row exists update all metrics
            cur.execute(f"INSERT INTO google_analytics_temp ({ins_query_dim}) "
                        f"VALUES ({ins_query_val}) "
                        f"ON CONFLICT (ga_viewID, ga_sourceMedium, ga_date, ga_campaign, ga_adcontent, ga_channelGrouping, ga_keyword) " 
                            f"DO "
                                f"UPDATE "
                                f"SET {upd_query}; ")
            conn.commit()
        print(str(row_count + 1) + ' row(s) inserted to DB')
       # close the communication with PostgreSQL
        cur.close()
    except (psycopg2.DatabaseError) as error:
        print('Database error')
        print(error)
        sys.exit(1)
    except(MemoryError) as error2:
        print('Out of memory')
        print(error2)
        sys.exit(1)
    finally:
        if conn is not None:
            conn.close()
    print('Database connection closed.')
    print('')

if __name__ == '__main__':
    print('Starting...')
    try:
        # read configuration from excel
        df_conf_base = pd.read_excel('google_analytics_conf_1.xlsx', sheet_name='base', header=0)
        df_conf_req = pd.read_excel('google_analytics_conf_1.xlsx', sheet_name='parameters', header=0)
        if len(df_conf_base) == 0:
            raise KeyError('No base data provided (view_id)')
        if pd.isna(df_conf_req['dimensions'].iloc[0]):
            raise KeyError('One or more dimensions missing')    
        for index, row in df_conf_req.iterrows():
            if pd.isna(row['metrics']):
                raise KeyError('One or more metrics missing')        
            if pd.isna(row['date_range']) and index < 2:
                raise KeyError('No date range provided')
        db_config(filename = 'database.ini')
        key_file_location = 'client_secrets.json'
        scopes = ['https://www.googleapis.com/auth/analytics.readonly']
    except(NameError, XLRDError, KeyError) as error:
        print('Error while reading configuration file(s)')
        print(error)
        sys.exit(1)      

    # iterate over view IDs
    for index, row in df_conf_base.iterrows():
        try:
            view_id = str(int(row['view_id']))
            print('View ID: ' + view_id)
        except(KeyError) as error:
            print('Could not read column')
            print(error)
            sys.exit(1)
        

        # call defined methods
        google_analytics_response = google_analytics(df_conf_req, view_id, key_file_location, scopes)
        df_response = google_analytics_response[0]
        dim_met_lst = google_analytics_response[1]

        postgre_write(df_response, dim_met_lst, view_id)
        print('Success')
            
          
        

Starting...
View ID: 166655749
Calling Google Analytics API...
Batch 1
524 row(s) received
Batch 2
524 row(s) received
Batch 3
524 row(s) received
Batch 4
524 row(s) received
Batch 5
524 row(s) received
Connecting to the PostgreSQL database...
Working...
524 row(s) inserted to DB
Database connection closed.

Success


In [51]:
df_response

ga:sourceMedium  \
0                              (direct) / (none)   
1                            15min.lt / referral   
2                         4corners.lt / referral   
3                                     adfp / rtb   
4                         away.vk.com / referral   
5                          barbora.lt / referral   
6                    beatosvirtuve.lt / referral   
7                                 bing / organic   
8                                 bing / organic   
9                                 bing / organic   
10                                bing / organic   
11                                bing / organic   
12                                bing / organic   
13                                bing / organic   
14                                bing / organic   
15                                bing / organic   
16                                bing / organic   
17                                bing / organic   
18                                bing / organic   
19                                bing / organic   
20                                bing / organic   
21                                bing / organic   
22                                bing / organic   
23                                bing / organic   
24                                bing / organic   
25                                bing / organic   
26                                bing / organic   
27                           brita.lt / referral   
28                      cannamella.lt / referral   
29                      click.mail.ru / referral   
30                  darzoviusultys.lt / referral   
31                                     dbm / cpm   
32                                     dfa / cpm   
33              digital_jacobs kapucino / banner   
34                       digital_persil / banner   
35                        digital_silan / banner   
36                              display / banner   
37                dk.search.yahoo.com / referral   
38                          duckduckgo / organic   
39                                   DV360 / cpc   
40                                   DV360 / cpc   
41             earn-money-with-seo.ga / referral   
42                          ecosia.org / organic   
43                          ecosia.org / organic   
44                           etech.lt / referral   
45                           facebook / carousel   
46                                facebook / cpc   
47                                facebook / cpc   
48                                facebook / cpc   
49                                facebook / cpc   
50                                facebook / cpc   
51                                facebook / cpc   
52                                facebook / cpc   
53                                facebook / cpc   
54                                facebook / cpc   
55                                facebook / cpc   
56                                facebook / cpc   
57                                facebook / cpc   
58                                facebook / cpm   
59                                facebook / cpm   
60                                Facebook / cpm   
61                       facebook.com / referral   
62                  fly.airbaltic.com / referral   
63                    gateway.opay.lt / referral   
64                       gencospor.tv / referral   
65                 geriausiadrauge.lt / referral   
66                     geroszuvies.lt / referral   
67              get-google-ranking.cf / referral   
68              get-google-ranking.tk / referral   
69                     getvilnius.com / referral   
70                         go.mail.ru / referral   
71                                  google / cpc   
72                                  google / cpc   
73                                  google / cpc   
74                                  google / cpc   
75                                  google / cpc   
76                           

In [59]:
import datetime
print(datetime.datetime.now())

2019-10-28 15:19:08.595178
